In [1]:
from submodules import Objects, Robots, Tasks, Users
from submodules.Scenes import Scene
from submodules.Actions import Actions
from submodules.Gestures import Gestures
from submodules.Users import Users
from model_noK import *
import numpy as np
from numpy import array as a

Firstly, let's go through iteration cycle
### 1. Gesture and actions setup

In [3]:
A = Actions.A
G = Gestures.G
U = Users.U
UID = Users.selected_id
print(A)
print(G)
print(U)
print(UID)

['move_up', 'open', 'put', 'pour', 'close', 'pick_up']
['swipe_up', 'open', 'swipe_back', 'hold', 'rotate', 'swipe_forward']
['Jan', 'Mara']
0


### 2. Generate policy
- Human Target action & Target object (**TaTo**) are the real values, which we want to determine
- Let's generate scene_state which is an input to the model
- And create_observations: `focus_point` and `gestures_vector` from TaTo
- Based on that we generate simple policy, which can be diagonal at start

In [4]:
TaTo = ('open', 'drawer')
scene_state = s.generate_scene_state(A, G, U, UID)

bn = MappingBayesNet(scene_state)
print(bn.create_observation(TaTo))
bn.init_policy_simple()

{'focus_point': array([[2.08299352, 0.03790751, 0.01821753]]), 'gesture_vec': array([0.19932437, 0.44597669, 0.10266543, 0.01188741, 0.11100262,
       0.12914349])}


{'CM_est': array([[1, 0, 0, 0, 0, 0],
        [0, 1, 0, 0, 0, 0],
        [0, 0, 1, 0, 0, 0],
        [0, 0, 0, 1, 0, 0],
        [0, 0, 0, 0, 1, 0],
        [0, 0, 0, 0, 0, 1]]),
 'i': 'init',
 'r': False,
 'permutation': 0}

### 3. Task
- Choose task and generate start (s) and target scenes (s2)

In [19]:
t = Tasks.CupToDrawer()
s, s2 = t.get_start_target_scenes()

In [20]:
s.info

Scene info. shape: [4, 4, 4]
cup, cup, [3 1 0], empty
drawer, drawer, [1 1 0], closed, []
Robot: [0 0 3], opened, rotation: 0, attached: -


In [21]:
s2.info

Scene info. shape: [4, 4, 4]
cup, cup, [3 1 0], empty
drawer, drawer, [1 1 0], opened, ['cup']
Robot: [0 0 3], opened, rotation: 0, attached: -


###  4. Select action
- Selects an action based on the observations

In [22]:
action = bn.select_action()
action

{'target_object': 'drawer', 'target_action': 'open'}

### 5. New world state
- Updates the scene


In [23]:
# temporary place
Actions.do(s, action, ignore_location=True)
s.drawer.info

drawer, drawer, [1 1 0], opened, []


### 6. Reward computation
- When reward is `True`, scenes are the same and task is done

In [24]:
s == s2

5.0

### 7. Complete the task as an action sequence

In [32]:
s, s2 = t.get_start_target_scenes()
reward = s == s2
print(f"Reward at the start: {reward}")

action_sequence = Tasks.CupToDrawer.action_sequence
for action_input in action_sequence:
    scene_state = s.generate_scene_state(A, G, U, UID)

    bn = MappingBayesNet(scene_state)
    bn.init_policy_simple()
    bn.create_observation(action_input)
    
    action = bn.select_action()
    print(action)
    
    if not Actions.do(s, action, ignore_location=True):
        raise Exception("Action cannot be executed")
    
    reward = s == s2
    print(f"Reward: {reward}")


Reward at the start: 4.0
{'target_object': 'drawer', 'target_action': 'open'}
Reward: 5.0
{'target_object': 'cup', 'target_action': 'pick_up'}
Reward: 5.0
{'target_object': 'drawer', 'target_action': 'put'}
Reward: True


In [33]:
s.info

Scene info. shape: [4, 4, 4]
cup, cup, [2 1 0], empty
drawer, drawer, [3 1 0], opened, ['cup']
Robot: [0 0 3], opened, rotation: 0, attached: -


# Attempt 1: Loop with reward

- prototype
- written notes and suggestions

In [37]:
# Static params
A = Actions.A
G = Gestures.G
U = Users.U
UID = Users.selected_id

# hyperparameters
alpha = 0.1
gamma = 0.6
epsilon = 0.1

In [38]:
# Task
t = Tasks.CupToDrawer()
# train loops 
n = 2
for i in range(1,n+1):
    epochs, penalties, reward, = 0, 0, 0
    done = False
    
    # Init. task start scene 's', target scene 's2'
    s, s2 = t.get_start_target_scenes()
    
    # Generate first scene state
    state = s.generate_scene_state(A, G, U, UID)
    bn = MappingBayesNet(state)
    bn.init_policy_simple()
    while not done:
        # Exploring actions space x Using learned values
        if np.random.uniform(0, 1) < epsilon:
            # There should be: Sampling from env/scene (p=10%)
            '''
            action = scene.sample()
            '''
            TaTo_action = t.decide(s)
        else:
            # There should be: Pick action using learned values (p=90%)
            '''
            action = np.argmax(q_table[state])
            '''
            TaTo_action = t.decide(s)
        
        
        print(f"Action: {TaTo_action}")
        # Apply action, compute reward, check if done
        s, reward, done, step_done = Actions.step(s, s2, TaTo_action, ignore_location=True)
        # Update policy based on reward
        bn.policy_update(reward)

Action: ('open', 'drawer')
Action: ('pick_up', 'cup')
Action: ('put', 'drawer')
Action: ('open', 'drawer')
Action: ('pick_up', 'cup')
Action: ('put', 'drawer')


In [39]:
s == s2

True

In [40]:
s.info

Scene info. shape: [4, 4, 4]
cup, cup, [3 1 0], empty
drawer, drawer, [1 3 0], opened, ['cup']
Robot: [0 0 3], opened, rotation: 0, attached: -


In [41]:
s2.info

Scene info. shape: [4, 4, 4]
cup, cup, [3 1 0], empty
drawer, drawer, [1 3 0], opened, ['cup']
Robot: [0 0 3], opened, rotation: 0, attached: -


In [42]:
s.drawer.contains_list

['cup']

In [43]:
bn.policy['CM_est']

array([[1, 0, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 0, 1, 0, 0],
       [0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 0],
       [0, 0, 0, 0, 0, 1]])

## Train the policy

In [45]:
#A = Actions.A = ['move_up', 'move_down', 'move_left', 'move_right', 'open', 'close']
policy = None
t = Tasks.CupToDrawer()

for i in range(1,2):
    epochs, penalties, reward, = 0, 0, 0
    done = False

    s, s2 = t.get_start_target_scenes()
    
    state = s.generate_scene_state(A, G, U, UID)
    bn = MappingBayesNet(state)
    bn.init_policy_simple(policy=policy)
    while not done:
        bn.create_observation(t.decide(s))
        action = bn.select_action()
        s, reward, done, step_done = Actions.step(s, s2, action, ignore_location=True, out=False)
        bn.policy_update(reward)
    bn.print_policy()
    policy = bn.policy

total: 4
0, r: False 	-> init, (open, drawer)
1, r: 5.0 	-> forward, (pick_up, cup)
2, r: 5.0 	-> forward, (put, drawer)
3, r: 5.0 	-> revert, (pick_up, cup)
d: done


In [46]:
bn.policy['CM_est']

array([[0, 0, 0, 0, 1, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0],
       [0, 0, 0, 1, 0, 0],
       [1, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 1]])

## Test the policy
- It trained a false policy

In [48]:
epochs, penalties, reward, = 0, 0, 0
done = False

s, s2 = t.get_start_target_scenes()
    
state = s.generate_scene_state(A, G, U, UID)
bn = MappingBayesNet(state)
bn.init_policy_simple()
steps = 0
while not done:
    bn.create_observation(t.decide(s))
    action = bn.select_action()
    s, reward, done, step_done = Actions.step(s, s2, action, ignore_location=True, out=False)
    steps += 1
bn.print_policy()

total: 1
0, r: False 	-> init, (put, drawer)
d: done


Policy change has no influence on the behavior 


In [49]:
bn.policy

{'CM_est': array([[1, 0, 0, 0, 0, 0],
        [0, 1, 0, 0, 0, 0],
        [0, 0, 1, 0, 0, 0],
        [0, 0, 0, 1, 0, 0],
        [0, 0, 0, 0, 1, 0],
        [0, 0, 0, 0, 0, 1]]),
 'i': 'init',
 'r': False,
 'action': {'target_object': 'drawer', 'target_action': 'put'}}

In [50]:
steps

3

Policy not trained well, error in the process. Assigning default policy

In [51]:
epochs, penalties, reward, = 0, 0, 0
done = False

s, s2 = t.get_start_target_scenes()
    
state = s.generate_scene_state(A, G, U, UID)
bn = MappingBayesNet(state)
bn.init_policy_simple()
steps = 0
while not done:
    bn.create_observation(t.decide(s))
    action = bn.select_action()
    s, reward, done, step_done = Actions.step(s, s2, action, ignore_location=True, out=False)
    bn.print_policy()
    steps += 1

total: 1
0, r: False 	-> init, (open, drawer)
d: done
total: 1
0, r: False 	-> init, (pick_up, cup)
d: done
total: 1
0, r: False 	-> init, (put, drawer)
d: done


In [52]:
bn.policy

{'CM_est': array([[1, 0, 0, 0, 0, 0],
        [0, 1, 0, 0, 0, 0],
        [0, 0, 1, 0, 0, 0],
        [0, 0, 0, 1, 0, 0],
        [0, 0, 0, 0, 1, 0],
        [0, 0, 0, 0, 0, 1]]),
 'i': 'init',
 'r': False,
 'action': {'target_object': 'drawer', 'target_action': 'put'}}

In [53]:
steps

3

# Troubleshooting

In [54]:
t = Tasks.CupToDrawer()
for i in range(1,101):
    epochs, penalties, reward, = 0, 0, 0
    done = False

    s, s2 = t.get_start_target_scenes()
    
    state = s.generate_scene_state(A, G, U, UID)
    bn = MappingBayesNet(state)
    bn.init_policy_simple()
    reward = 0.
    while not done:
        bn.create_observation(t.decide(s))
        action = bn.select_action()
        s, reward, done, step_done = Actions.step(s, s2, action, ignore_location=True, out=False)
        bn.policy_update(reward, out=True)
        if not step_done: reward = -999

r: 5.0, diff: 1e-08
r: 5.0, diff: 0.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

...

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff: -1.0
r: 4.0, diff

In [59]:
bn.policy

{'CM_est': array([[0, 0, 0, 0, 0, 1],
        [0, 0, 0, 0, 1, 0],
        [0, 1, 0, 0, 0, 0],
        [0, 0, 0, 1, 0, 0],
        [0, 0, 1, 0, 0, 0],
        [1, 0, 0, 0, 0, 0]]),
 'i': 'revert',
 'r': 5.0,
 'action': {'target_object': 'drawer', 'target_action': 'close'}}

Here it returned the diagonal matrix, which is correct.

Diagonal array policy is optimal in this setup.
Learning should reject all mutations of policy array.

In [60]:
A

['move_up', 'open', 'put', 'pour', 'close', 'pick_up']

The criterium, that policy is correct or the best possible can be measured by steps, which are needed to make the task done.

## Single run, without changing parameters

In [62]:
t = Tasks.CupToDrawer()
policy = None
for i in range(1,2):
    epochs, penalties, reward = 0,0,0
    done = False
    
    s, s2 = t.get_start_target_scenes()
    
    state = s.generate_scene_state(A, G, U, UID)
    bn = MappingBayesNet(state)
    bn.init_policy_simple(policy)
    reward = 0.
    while not done:
        bn.create_observation(t.decide(s))
        action = bn.select_action()
        s, reward, done, step_done = Actions.step(s, s2, action, ignore_location=True, out=False)
        bn.policy_step()
        if not step_done:
            reward = -999
    bn.print_policy()
    policy = bn.policy_update(reward=-len(bn.policy_history), out=True)

total: 4
0, r: False 	-> init, (open, drawer)
1, r: 0.0 	-> init, (pick_up, cup)
2, r: 0.0 	-> init, (put, drawer)
3, r: 0.0 	-> init, (put, drawer)
d: done
r: -4, diff: -4.0


## Multiple epochs
- Learning base on n of actions after every run

In [63]:
def policy_update(bn, epoch_history):
    reward = -len(bn.policy_history)
    if epoch_history != []:
        reward_dif = reward - epoch_history[-1]['r']
    else:
        reward_dif = 0.00000001

    policy = deepcopy(bn.policy) # new policy
    policy['r'] = reward
    if reward_dif >= 0:
        r1,r2 = np.random.choice(len(bn.A), 2, replace=False)
        policy['CM_est'][[r1,r2]] = policy['CM_est'][[r2,r1]]
        policy['i'] = 'forward'
    else: # Rewrites the policy from history, it has its own reward tag saved
        policy = deepcopy(epoch_history[-2])
        policy['i'] = 'revert'

    epoch_history.append(deepcopy(policy))
    return policy

A = Actions.A
G = Gestures.G
epoch_history = []
t = Tasks.CupToDrawer()
policy = {'CM_est': np.array([[0, 1, 0, 0, 0, 0],
        [1, 0, 0, 0, 0, 0],
        [0, 0, 1, 0, 0, 0],
        [0, 0, 0, 1, 0, 0],
        [0, 0, 0, 0, 1, 0],
        [0, 0, 0, 0, 0, 1]]),
 'i': 'revert',
 'r': -52}
for i in range(1,1001):
    epochs, penalties, reward = 0,0,0
    done = False
    
    s, s2 = t.get_start_target_scenes()
    
    state = s.generate_scene_state(A, G, U, UID)
    bn = MappingBayesNet(state)
    bn.init_policy_simple(policy=policy)
    if i == 1: 
        epoch_history.append(deepcopy(bn.policy))
        epoch_history.append(deepcopy(bn.policy))
        
    reward = 0.
    n=0
    while not done:
        bn.create_observation(t.decide(s))
        action = bn.select_action()
        s, reward, done, step_done = Actions.step(s, s2, action, ignore_location=True, out=False)
        bn.policy_step(reward)
        if not step_done:
            reward = -999
        n+=1
        if n>50: break
    policy = policy_update(bn, epoch_history)

In [64]:
epoch_history

[{'CM_est': array([[0, 1, 0, 0, 0, 0],
         [1, 0, 0, 0, 0, 0],
         [0, 0, 1, 0, 0, 0],
         [0, 0, 0, 1, 0, 0],
         [0, 0, 0, 0, 1, 0],
         [0, 0, 0, 0, 0, 1]]),
  'i': 'revert',
  'r': -52},
 {'CM_est': array([[0, 1, 0, 0, 0, 0],
         [1, 0, 0, 0, 0, 0],
         [0, 0, 1, 0, 0, 0],
         [0, 0, 0, 1, 0, 0],
         [0, 0, 0, 0, 1, 0],
         [0, 0, 0, 0, 0, 1]]),
  'i': 'revert',
  'r': -52},
 {'CM_est': array([[0, 1, 0, 0, 0, 0],
         [0, 0, 1, 0, 0, 0],
         [1, 0, 0, 0, 0, 0],
         [0, 0, 0, 1, 0, 0],
         [0, 0, 0, 0, 1, 0],
         [0, 0, 0, 0, 0, 1]]),
  'i': 'forward',
  'r': -52,
  'action': {'target_object': 'drawer', 'target_action': 'move_up'}},
 {'CM_est': array([[0, 1, 0, 0, 0, 0],
         [0, 0, 1, 0, 0, 0],
         [1, 0, 0, 0, 0, 0],
         [0, 0, 0, 0, 1, 0],
         [0, 0, 0, 1, 0, 0],
         [0, 0, 0, 0, 0, 1]]),
  'i': 'forward',
  'r': -52,
  'action': {'target_object': 'drawer', 'target_action': 'pick_up'

In [67]:
policy

{'CM_est': array([[1, 0, 0, 0, 0, 0],
        [0, 0, 0, 1, 0, 0],
        [0, 0, 1, 0, 0, 0],
        [0, 1, 0, 0, 0, 0],
        [0, 0, 0, 0, 1, 0],
        [0, 0, 0, 0, 0, 1]]),
 'i': 'forward',
 'r': -4,
 'action': {'target_object': 'drawer', 'target_action': 'put'}}

Algorithm won't learn.
I will try to reduce actions, try to simplify and see what is going on:

In [72]:
import importlib
import model_noK_evensimplified
importlib.reload(model_noK_evensimplified)

from model_noK_evensimplified import MappingBayesNet_EvenSimplified

In [55]:
def policy_update(bn, epoch_history):
    reward = -len(bn.policy_history)
    if epoch_history != []:
        reward_dif = reward - epoch_history[-1]['r']
    else:
        reward_dif = 0.00000001

    policy = deepcopy(bn.policy) # new policy
    policy['r'] = reward
    if reward_dif >= 0:
        r1,r2 = np.random.choice(len(bn.A), 2, replace=False)
        policy['CM_est'][[r1,r2]] = policy['CM_est'][[r2,r1]]
        policy['i'] = 'forward'
    else: # Rewrites the policy from history, it has its own reward tag saved
        policy = deepcopy(epoch_history[-2])
        policy['i'] = 'revert'

    epoch_history.append(deepcopy(policy))
    return policy

A = ['pick_up', 'put', 'open']
G = ['swipe_up', 'swipe_down','open']

epoch_history = []
t = Tasks.CupToDrawer()
policy = {'CM_est': np.array([[0, 1, 0],
                              [1, 0, 0],
                              [0, 0, 1]]), 'i': 'revert', 'r': -52}
for i in range(1,101):
    s, s2 = t.get_start_target_scenes()
    
    state = s.generate_scene_state(A, G, U, UID)
    bn = MappingBayesNet_EvenSimplified(state)
    bn.init_policy_simple(policy=policy)
    if i == 1: epoch_history.append(deepcopy(bn.policy))
    reward = 0.
    n=0
    done = False
    while not done:
        bn.create_observation(t.decide(s))
        action = bn.select_action()
        s, reward, done, step_done = Actions.step(s, s2, action, ignore_location=True, out=False)
        bn.policy_step(reward)
        if not step_done:
            reward = -999
        n+=1
        if n>50: break
    policy = policy_update(bn, epoch_history)


NameError: name 'MappingBayesNet_EvenSimplified' is not defined

In [ ]:
bn.print_policy()

In [ ]:
bn.policy

In [45]:
bn.observation

{'focus_point': array([[2.93877491, 0.92716399, 0.01230508]]),
 'gesture_vec': array([0.06349322, 0.05235054, 0.63612513, 0.01739451, 0.13388376,
        0.09675284])}

In [46]:
action

{'target_object': 'drawer', 'target_action': 'put'}